
##Running common notebook to get access to variables

In [0]:
%run "/Workspace/Users/schaudhuri1495@gmail.com/04. Common"

In [0]:
dbutils.widgets.text(name = "env", defaultValue = '', label = 'Enter the environment in lowercase')
env = dbutils.widgets.get("env")


## Reading data from Silver_Traffic table

In [0]:
def read_from_silver_traffic_table(env):
    print('Reading the Silver raw_traffic data table : ', end='')
    df_silverTraffic = (spark.readStream
                        .table(f"`databricks_{env}_ws`.`silver`.silver_traffic"))
    
    print(f"Reading databricks_{env}_ws.silver.silver_traffic Success!!")

    return(df_silverTraffic)


## Reading data from Silver_Roads table

In [0]:
def read_from_silver_roads_table(env):
    print('Reading the Silver raw_roads data table : ', end='')
    df_silverRoads = (spark.readStream
                        .table(f"`databricks_{env}_ws`.`silver`.silver_roads"))
    
    print(f"Reading databricks_{env}_ws.silver.silver_roads Success!!")

    return(df_silverRoads)


## Creating a column named 'Vehicle_Intensity'

In [0]:
def creating_vehicle_intensity(df):
    print("Inside function to create Vehicle_Intensity column")
    from pyspark.sql.functions import when, col

    df_vehicle_intensity = df.withColumn("Vehicle_Intensity",
                  col('Motor_Vehicles_Count') / col('Link_Length_km')
                  )
    print("SUCCESS!!!!")

    return df_vehicle_intensity


##Creating Load_Time Column

In [0]:
def create_load_time(df):
    print("Inside the create load_time Function")

    from pyspark.sql.functions import current_timestamp

    df_load_time = df.withColumn('Load_Time', current_timestamp()) 

    print("SUCCESS FROM create_load_time FUNCTION!!!!!!!!")
    
    return(df_load_time)


##Writing the transformed data to Gold_Traffic table in Gold schema

In [0]:
def write_traffic_goldTable(StreamingDF, env):

    print("Writing the silver_traffic Data : ", end='')
    write_stream_gold = (StreamingDF.writeStream
                            .format('delta')
                            .option("checkpointLocation",checkpoints+'/GoldTrafficLoad/Checkpt')
                            .outputMode('append')
                            .queryName('GoldTrafficWriteStream')
                            .trigger(availableNow=True)
                            .toTable(f"`databricks_{env}_ws`.`gold`.`gold_traffic`"))

    write_stream_gold.awaitTermination()
    print(f"Writing databricks_{env}_ws.gold.gold_traffic SUCCESS!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!")


##Writing the transformed data to Gold_Roads table in Gold schema

In [0]:
def write_roads_goldTable(StreamingDF, env):
    print("Writing the gold_roads Data : ", end='')
    
    write_stream_roads_gold = (StreamingDF.writeStream
                            .format('delta')
                            .option("checkpointLocation",checkpoints+'/GoldRoadsLoad/Checkpt')
                            .outputMode('append')
                            .queryName('GoldRoadscWriteStream')
                            .trigger(availableNow=True)
                            .toTable(f"`databricks_{env}_ws`.`gold`.`gold_roads`"))

    write_stream_roads_gold.awaitTermination()
    print(f"Writing databricks_{env}_ws.gold.gold_roads SUCCESS!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!")

##Calling all functions

In [0]:
#Reading from silver tables

df_silverTraffic = read_from_silver_traffic_table(env)
df_silverRoads = read_from_silver_roads_table(env)

#Transformations
df_gold_intensity = creating_vehicle_intensity(df_silverTraffic)
df_gold_final_traffic = create_load_time(df_silverTraffic)
df_gold_final_roads = create_load_time(df_silverRoads)

#Writing to gold tables
write_traffic_goldTable(df_gold_final_traffic, env)
write_roads_goldTable(df_gold_final_roads, env)

Reading the Silver raw_traffic data table : Reading databricks_dev_ws.silver.silver_traffic Success!!
Reading the Silver raw_roads data table : Reading databricks_dev_ws.silver.silver_roads Success!!
Inside function to create Vehicle_Intensity column
SUCCESS!!!!
Inside the create load_time Function
SUCCESS FROM create_load_time FUNCTION!!!!!!!!
Inside the create load_time Function
SUCCESS FROM create_load_time FUNCTION!!!!!!!!
Writing the silver_traffic Data : Writing databricks_dev_ws.gold.gold_traffic SUCCESS!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
Writing the gold_roads Data : Writing databricks_dev_ws.gold.gold_roads SUCCESS!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!


In [0]:
%sql
select * from databricks_dev_ws.gold.gold_traffic

Record_ID Count_point_id Direction_of_travel Year Count_date hour Region_id Region_name Local_authority_name Road_name Road_Category_ID Start_junction_road_name End_junction_road_name Latitude Longitude Link_length_km Pedal_cycles Two_wheeled_motor_vehicles Cars_and_taxis Buses_and_coaches LGV_Type HGV_Type EV_Car EV_Bike Extract_Time Electric_Vehicle_Count motor_vehicles_count Transformed_Time Load_Time 18656 37625 E 2014 9/10/2014 0:00 13 7 East of England Suffolk A1302 4 A134 A143 52.23534253 0.72243571 1.3 4 6 324 5 36 3 0 0 2024-07-15T18:09:56.809Z 0 374 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 18828 20511 N 2014 5/20/2014 0:00 17 4 Wales Monmouthshire A40 3 B4293 A466 51.80987719 -2.712139559 0.8 1 4 1050 2 98 15 5 1 2024-07-15T18:09:56.809Z 6 1175 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 19067 37918 S 2014 9/11/2014 0:00 13 9 South East Surrey M25 1 12 11 51.38551118 -0.521223429 3.5 0 23 4253 11 984 141 24 33 2024-07-15T18:09:56.809Z 57 5469 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 19244 36213 W 2014 10/17/2014 0:00 12 6 London Redbridge A12 4 A1400/A123 Rndbt - Cranbrook Road LA boundary 51.57519529 0.091047733 4.9 1 20 1290 19 218 65 5 12 2024-07-15T18:09:56.809Z 17 1629 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 19304 46209 N 2014 5/14/2014 0:00 18 7 East of England Essex A12 3 B1024 B1024S 51.82769228 0.700677657 4.5 0 25 1544 5 284 17 5 4 2024-07-15T18:09:56.809Z 9 1884 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 19365 50573 N 2014 5/16/2014 0:00 13 4 Wales Newport A4072 4 M4 Junction 28 A468 Forge Road 51.57221335 -3.04029338 1.2 5 10 1130 10 140 30 5 4 2024-07-15T18:09:56.809Z 9 1329 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 19439 27294 E 2014 7/1/2014 0:00 15 5 North West Manchester A560 4 LA Boundary M56 53.40104222 -2.302267716 2.7 7 8 817 15 131 13 0 0 2024-07-15T18:09:56.809Z 0 984 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 19980 16021 N 2014 10/7/2014 0:00 7 1 South West North Somerset M5 1 LA Boundary 21 51.31326357 -2.885205029 7.9 0 7 1912 6 433 46 8 5 2024-07-15T18:09:56.809Z 13 2417 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 20183 26121 W 2014 5/19/2014 0:00 18 9 South East Reading A4 4 Burghfield Rd Honey End Lane 51.44449111 -1.017193502 0.3 25 4 472 5 35 2 0 2 2024-07-15T18:09:56.809Z 2 520 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 20452 46083 S 2014 9/3/2014 0:00 15 2 East Midlands Lincolnshire A1 3 A151/B676 B1174 52.85957043 -0.629060923 8.4 0 5 983 4 194 39 8 5 2024-07-15T18:09:56.809Z 13 1238 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 20474 36564 W 2014 6/16/2014 0:00 13 2 East Midlands Derbyshire A52 3 LA Boundary M1 52.91186454 -1.327319052 6.1 0 5 961 8 190 37 3 10 2024-07-15T18:09:56.809Z 13 1214 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 20819 47578 W 2014 6/17/2014 0:00 8 7 East of England Hertfordshire M25 1 23 24 51.68547857 -0.194499226 4.2 0 27 3662 9 790 149 29 24 2024-07-15T18:09:56.809Z 53 4690 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 21174 8017 N 2014 7/1/2014 0:00 10 1 South West Somerset A358 4 A303 A378 50.96561123 -2.998200521 10.2 1 3 562 2 113 27 8 10 2024-07-15T18:09:56.809Z 18 725 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 21436 46491 W 2014 5/8/2014 0:00 11 7 East of England Cambridgeshire A14 3 A14 merge B1049 52.23313286 0.09254297 2.4 0 2 1249 0 323 85 15 10 2024-07-15T18:09:56.809Z 25 1684 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 21494 46416 E 2014 4/23/2014 0:00 9 1 South West Devon A38 3 A383 A382 Newton Road 50.54316907 -3.694922412 5.7 0 4 902 2 263 35 18 11 2024-07-15T18:09:56.809Z 29 1235 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 21737 26081 E 2014 10/2/2014 0:00 9 6 London Barnet A1 4 A5100 A41/A5109 51.62102531 -0.253557068 0.9 3 28 993 12 315 101 8 11 2024-07-15T18:09:56.809Z 19 1468 2024-07-15T20:36:04.239Z 2024-07-17T06:13:32.61Z 22169 16309 W 2014 5/12/2014 0:00 7 9 South East Hampshire A31 4 A32 A339 51.13600647 -0.989452241 1.3 0 7 576 2 143 25 3 7 2024

In [0]:
%sql
select * from databricks_dev_ws.gold.gold_roads

Road_ID Road_Category_Id Road_Category Region_ID Region_Name Total_Link_Length_Km Total_Link_Length_Miles All_Motor_Vehicles Road_Category_Name Road_Type Load_Time 75 1 TM 7 East of England 245.9 152.8 4.120104199E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 44 5 M 10 West Midlands 27956.1 17371.12 9.927697665E9 Class B road Minor 2024-07-17T06:13:53.149Z 28 4 PA 7 East of England 2719.344 1689.72 7.493977513E9 Class A Principle Road Major 2024-07-17T06:13:53.149Z 33 4 PA 8 Yorkshire and the Humber 2559.104 1590.15 6.365559059E9 Class A Principle Road Major 2024-07-17T06:13:53.149Z 40 1 TM 10 West Midlands 351.963 218.7 5.280343918E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 39 5 M 9 South East 40851.1 25383.7 1.5597621429E10 Class B road Minor 2024-07-17T06:13:53.149Z 55 3 TA 2 East Midlands 1215.788 755.46 5.056721458E9 Class A Trunk Road Major 2024-07-17T06:13:53.149Z 52 4 PA 1 South West 3882.154 2412.26 8.028746829E9 Class A Principle Road Major 2024-07-17T06:13:53.149Z 71 1 TM 6 London 66.386 41.25 1.311689053E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 66 1 TM 5 North West 558.839 347.25 7.370068617E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 5 1 TM 2 East Midlands 178.609 110.98 2.73666152E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 6 3 TA 2 East Midlands 1219.231 757.6 4.936702686E9 Class A Trunk Road Major 2024-07-17T06:13:53.149Z 41 2 PM 10 West Midlands 6.895 4.28 1.464122624E8 Class A Principle Motorway Major 2024-07-17T06:13:53.149Z 59 3 TA 3 Scotland 2813.698 1748.35 5.19258696E9 Class A Trunk Road Major 2024-07-17T06:13:53.149Z 13 1 TM 4 Wales 130.291 80.96 1.306589845E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 60 4 PA 3 Scotland 7419.724 4610.4 6.67873035E9 Class A Principle Road Major 2024-07-17T06:13:53.149Z 16 5 M 4 Wales 28322.4 17598.72 5.286183479E9 Class B road Minor 2024-07-17T06:13:53.149Z 56 4 PA 2 East Midlands 2575.861 1600.57 5.66881734E9 Class A Principle Road Major 2024-07-17T06:13:53.149Z 29 5 M 7 East of England 34610.8 21506.15 1.1083436184E10 Class B road Minor 2024-07-17T06:13:53.149Z 10 3 TA 3 Scotland 2820.302 1752.45 5.05292557E9 Class A Trunk Road Major 2024-07-17T06:13:53.149Z 37 3 TA 9 South East 855.597 531.64 5.54362878E9 Class A Trunk Road Major 2024-07-17T06:13:53.149Z 54 1 TM 2 East Midlands 180.352 112.07 2.842352469E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 8 5 M 2 East Midlands 26712.7 16598.5 7.083362916E9 Class B road Minor 2024-07-17T06:13:53.149Z 49 5 M 11 North East 14025.9 8715.29 4.664291984E9 Class B road Minor 2024-07-17T06:13:53.149Z 74 5 M 6 London 12609.0 7834.87 6.938861113E9 Class B road Minor 2024-07-17T06:13:53.149Z 21 5 M 5 North West 31405.9 19514.72 1.0232738407E10 Class B road Minor 2024-07-17T06:13:53.149Z 15 4 PA 4 Wales 2581.176 1603.87 4.010930618E9 Class A Principle Road Major 2024-07-17T06:13:53.149Z 22 1 TM 6 London 65.744 40.85 1.245269582E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 53 5 M 1 South West 43659.6 27128.82 9.272591264E9 Class B road Minor 2024-07-17T06:13:53.149Z 38 4 PA 9 South East 4269.653 2653.04 1.2858678243E10 Class A Principle Road Major 2024-07-17T06:13:53.149Z 58 1 TM 3 Scotland 338.535 210.36 2.577081643E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 1 1 TM 1 South West 301.339 187.24 3.465840186E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 68 3 TA 5 North West 823.653 511.79 2.750751747E9 Class A Trunk Road Major 2024-07-17T06:13:53.149Z 62 1 TM 4 Wales 131.563 81.75 1.350418388E9 Class A Trunk Motor Major 2024-07-17T06:13:53.149Z 48 4 PA 11 North East 1301.91 808.97 3.108413973E9 Class A Principle Road Major 2024-07-17T06:13:53.149Z 23 3 TA 6 London 339.479 210.94 3.913260559E9 Class A Trunk Road Major 2024-07-17T06:13:53.149Z 2 3 TA 1 South West 993.586 617.39 3.48471021E9 Class A Trunk Road Major 2024-07-17T06:13:53.149Z 32 3 TA 8 Yorkshire and the Humber 703.57 437.18 2.966722872E9 Class A Trunk Road Major 2024-07-17T06:13:53.149Z 51 3